In [8]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [6]:
!ls

README.md                 model_checkpoints         recommender.py
app.py                    notebooks                 requirements.txt
data                      orchestrate_audio_data.py src


In [7]:
import numpy as np
import librosa
import torch
from src import laion_clap
from glob import glob
import pandas as pd


In [ ]:
model = laion_clap.CLAP_Module(enable_fusion=False, amodel= 'HTSAT-base')
model.load_ckpt(ckpt="music_audioset_epoch_15_esc_90.14.pt")

In [11]:
def load_music_file(file_name):
    audio_data, _ = librosa.load(file_name, sr=48000) # sample rate should be 48000
    audio_data = audio_data.reshape(1, -1) # Make it (1,T) or (N,T)
    # audio_data = torch.from_numpy(int16_to_float32(float32_to_int16(audio_data))).float() # quantize before send it in to the model
    with torch.no_grad():
        audio_embed = model.get_audio_embedding_from_data(x = audio_data, use_tensor=False)
    return audio_embed


In [9]:
music_files = glob("/Users/berkayg/Codes/music-project/AudioCLIP/data/downloaded_tracks/*.wav")

In [14]:
import pickle
with open("/Users/berkayg/Codes/music-project/laion-clap-project/curate-me-a-playlist/data/vectors/song_names.pkl", "rb") as reader:
    ls = pickle.load(reader)


['Pink Floyd - The Great Gig In The Sky - 2011 Remastered Version.wav',
 'Aretha Franklin - The House That Jack Built.wav',
 'The Beatles - I Saw Her Standing There - Remastered.wav',
 'Cem Karaca - Çok Yorgunum.wav',
 'Mert Fırat - Bana Göre Değil.wav',
 'Santana - Whole Lotta Love (feat. Chris Cornell).wav',
 'MIKA - Relax, Take It Easy.wav',
 'Adamlar - Bi Öyle Bi Böyle.wav',
 "Blue Öyster Cult - (Don't Fear) The Reaper.wav",
 'Bob Dylan - The Man in Me.wav',
 'Buena Vista Social Club - Tiene Sabor.wav',
 'Gnarls Barkley - Crazy.wav',
 "Guns N' Roses - Knockin' On Heaven's Door.wav",
 'Gevende - Esinti.wav',
 'Mazhar Alanson - Bu Ne Biçim Hikaye Böyle.wav',
 'Bon Jovi - Dry County.wav',
 'Muse - Starlight.wav',
 'Eric Clapton - Riding with the King.wav',
 'Nina Simone - Feeling Good.wav',
 'The Dø - Too Insistent.wav',
 'Guthrie Govan - Lost in Rio.wav',
 'Gipsy Kings - Volare (Nel Blu di Pinto di Blu).wav',
 'Cem Karaca - Dadaloğlu.wav',
 'Pixies - Where Is My Mind?.wav',
 'mor ve 

In [13]:
music_data = np.zeros((len(music_files), 512), dtype=np.float32)
for m in range(music_data.shape[0]):
    music_data[m] = load_music_file(music_files[m])


/var/folders/sr/r72219hj06x_1xvw7hhd517h0000gn/T/ipykernel_18860/3009710654.py:2: UserWarning: PySoundFile failed. Trying audioread instead.
  audio_data, _ = librosa.load(file_name, sr=48000) # sample rate should be 48000
/Users/berkayg/miniforge3/envs/playlist-curator/lib/python3.10/site-packages/librosa/core/audio.py:183: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)


In [14]:
text_data = ["This audio is a romantic song"] 
text_embed = model.get_text_embedding(text_data)
print(text_embed.shape)

(1, 512)


In [10]:
song_names = [k.split("/")[-1] for k in music_files]

In [16]:
with torch.no_grad():
    ranking = torch.tensor(music_data) @ torch.tensor(text_embed).t()
    ranking = ranking[:, 0].reshape(-1, 1)
print(ranking.shape)

torch.Size([100, 1])


In [14]:
pd.DataFrame(ranking, columns=[text_data[0]], index=song_names).nlargest(15, text_data[0])

This audio is a romantic song
Coldplay - Charlie Brown.wav                                             0.400684
Sam Smith - I'm Not The Only One.wav                                     0.373561
Pink Floyd - The Great Gig In The Sky - 2011 Re...                       0.371584
Christina Aguilera - You Lost Me.wav                                     0.370390
Lana Del Rey - Yayo.wav                                                  0.370379
Queen - It's A Hard Life - Remastered 2011.wav                           0.348699
Teoman - Haziran.wav                                                     0.331220
John Lennon - Imagine - Remastered 2010.wav                              0.330397
Sleeping At Last - Mars.wav                                              0.328770
Adele - Someone Like You.wav                                             0.325650
Coldplay - What If.wav                                                   0.315717
Adamlar - Orda Ortada.wav                                                0.306465
Eric Clapton - Autumn Leaves.wav                                         0.305451
Premiata Forneria Marconi - Impressioni di sett...                       0.295878
Guthrie Govan - Lost in Rio.wav                                          0.284883